# 演练场
此笔记本将带你了解 repomgr 与 particles 对象相关操作

# 从一个例子开始
## 了解文件结构
了解一下文件结构

In [ ]:
!tree # 了解文件结构

如果你先前运行了单元格, 请运行下面一格清理.

In [ ]:
!rm -rf test_new_repo
!rm -rf heurams.log*

## 导入模块
导入所需模块, 你会看到欢迎信息, 标示了库所使用的配置.  
HeurAMS 在基础设施也使用配置文件实现隐式的依赖注入.  

In [ ]:
import heurams.kernel.repolib as repolib # 这是 RepoLib 子模块, 用于管理和结构化 repo(中文含义: 仓库) 数据结构与本地文件间的联系
import heurams.kernel.particles as pt # 这是 Particles(中文含义: 粒子) 子模块, 用于运行时的记忆管理操作
from pathlib import Path # 这是 Python 的 Pathlib 模块, 用于表示文件路径, 在整个项目中, 都使用此模块表示路径

## 运行时检查
如你所见, repo 在文件系统内存储为一个文件夹.  
因此在载入之前, 首先要检查这是否是一个合乎标准的 repo 文件夹.  

In [ ]:
is_vaild = repolib.Repo.check_repodir(Path("./test_repo"))
print(f"这是一个 {'合规' if is_vaild else '不合规'} 的 repo!")

## 加载仓库
接下来, 正式加载 repo.

In [ ]:
test_repo = repolib.Repo.create_from_repodir(Path("./test_repo"))

## 导出为字典
作为一个数据容器, repo 相应地建立了导入和导出的功能.  
我们刚刚从本地文件夹导入了一个 repo.  
现在试试导出为一个字典.

In [ ]:
test_repo_dic = test_repo.export_to_single_dict()
from pprint import pprint
pprint(test_repo_dic)

## 持久化与部分保存
如你所见, 所有内容被结构化地输出了!  

现在写回到文件夹!  

我们注意到, 并非所有的内容都要被修改.  
我们可以只保存接受修改的一部分, 默认情况下, 是迭代的记忆数据(algodata).  
这就是为什么我们一般不使用单个 json 或 toml 来存储 repo.

persist_to_repodir 接受两个可选参数: 
- save_list: 默认为 ["algodata"], 是要持久化的数据.
- source: 默认为原目录, 你也可以手动指定为其他文件夹(通过 Path)

现在做一些演练, 我们将创建一个位于 test_new_repo 的"克隆", 此时我们!
除非文件夹已经存在, Repo 对象将会为你自动创建新文件夹.

In [ ]:
test_repo.persist_to_repodir(save_list=["schedule", "payload", "manifest", "typedef", "algodata"], source=Path("test_new_repo"))
!tree

如你所见, test_new_repo 已被生成!

# 数据结构
现在讲解 repo 的数据结构

## Lict 对象
Lict 对象集成了部分列表和字典的功能, 数据在这两种风格的 API 间都可用, 且修改是同步的.  
Lict 默认情况下不会保存序列顺序, 而是在列表形式下, 自动按索引字符序排布, 详情请参阅源代码.  
现在导入并初始化一个 Lict 对象:

In [ ]:
from heurams.utils.lict import Lict
lct = Lict() # 空的
lct = Lict(initlist=[("name", "tom"), ("age", 12), ("enemy", "jerry")]) # 基于列表
print(lct)
lct = Lict(initdict={"name": "tom", "age": 12, "enemy": "jerry"}) # 基于字典
print(lct)


### 输出形式
lct 的"官方"输出形式是列表形式
你也可以选择输出字典形式

In [ ]:
print(lct.dicted_data)

### dicted_data 属性与修改方式
dicted_data 属性是一个字典, 它自动同步来自 Lict 对象操作的修改.
一个注意事项: 不要直接修改 dicted_data, 这将不会触发同步 hook.
如果你一定要这样做, 请在完事后手动运行同步 hook.
推荐的修改方式是直接把 lct 当作一个字典

In [ ]:
# 由于 jupyter 的环境处理, 请不要重复运行此单元格, 如果想再看一遍, 请重启 jupyter 后再全部运行

# 错误的方式
lct.dicted_data["type"] = "cat"
print(lct) # 将不会同步修改

# 不推荐, 但可用的方式
lct.dicted_data["type"] = "cat"
lct._sync_based_on_dict()
print(lct)

# 推荐方式
lct['is_human'] = False
print(lct)

### data 属性与修改方式
data 属性是一个列表, 它自动同步来自 Lict 对象操作的修改.
一个注意事项: 不要直接修改 data, 这将不会触发同步 hook, 并且可能破坏排序.
如果你一定要这样做, 请在完事后手动运行同步 hook 和 sort, 此处不演示.
推荐的修改方式是直接把 lct 当作一个列表, 且避免使用索引修改

In [ ]:
# 由于 jupyter 的环境处理, 请不要重复运行此单元格, 如果想再看一遍, 请重启 jupyter 后再全部运行

# 唯一推荐方式
lct.append(('enemy_2', 'spike'))
print(lct.dicted_data)

### 多面手
Lict 有一些很酷的功能
详情请看源文件
此处是一些例子

In [ ]:
lct = Lict(initdict={'age': 12, 'enemy': 'jerry', 'is_human': False, 'name': 'tom', 'type': 'cat', 'enemy_2': 'spike'})
print(lct)
print(lct.dicted_data)
print("------")
for i in lct:
    print(i)
print(len(lct))
while len(lct) > 0:
    print(lct.pop())
    print(lct)
lct = Lict(initdict={'age': 12, 'enemy': 'jerry', 'is_human': False, 'name': 'tom', 'type': 'cat', 'enemy_2': 'spike'})
...

关爱环境 从你我做起

In [ ]:
!rm -rf test_new_repo
!rm -rf heurams.log*